<a href="https://colab.research.google.com/github/FathirAMM/Celetial_Minds_Predicta_1.0/blob/main/Copy_of_Challange_1_Weather_forecasting_.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!nvidia-smi  # this should display information about available GPUs

Sun Jun 23 03:27:26 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   41C    P8              12W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [ ]:
# ! pip install cudf-cu11 index-url=https://pypi.nvidia.com # latest cudf

In [ ]:
%load_ext cudf.pandas

In [ ]:
import pandas as pd

In [ ]:
# Load the historical weather data
file_path = '/content/historical_weather.csv'
data = pd.read_csv(file_path)

# Display the first few rows of the dataset
data.head()

city_id        date  avg_temp_c  min_temp_c  max_temp_c precipitation_mm  \
0    C001  2014-01-01         6.6        -1.4        11.6             <NA>   
1    C001  2014-01-02         9.3         6.3        13.3             <NA>   
2    C001  2014-01-03         7.6         1.9        14.0             <NA>   
3    C001  2014-01-04         7.6         3.9        13.3             <NA>   
4    C001  2014-01-05         8.6         0.5        16.9             <NA>   

  snow_depth_mm avg_wind_dir_deg  avg_wind_speed_kmh  
0          <NA>            168.0                 6.2  
1          <NA>            155.0                10.0  
2          <NA>             <NA>                 5.8  
3          <NA>            291.0                11.3  
4          <NA>             <NA>                 5.0

In [ ]:
# summary information to understand its structure
data.info()

<class 'cudf.core.dataframe.DataFrame'>
RangeIndex: 182338 entries, 0 to 182337
Data columns (total 9 columns):
 #   Column              Non-Null Count   Dtype
---  ------              --------------   -----
 0   city_id             182338 non-null  object
 1   date                182338 non-null  object
 2   avg_temp_c          181114 non-null  float64
 3   min_temp_c          176452 non-null  float64
 4   max_temp_c          174845 non-null  float64
 5   precipitation_mm    112594 non-null  float64
 6   snow_depth_mm       12238 non-null   float64
 7   avg_wind_dir_deg    146944 non-null  float64
 8   avg_wind_speed_kmh  159866 non-null  float64
dtypes: float64(7), object(2)
memory usage: 13.7+ MB


In [ ]:
# null values
data.isnull().sum()

city_id                    0
date                       0
avg_temp_c              1224
min_temp_c              5886
max_temp_c              7493
precipitation_mm       69744
snow_depth_mm         170100
avg_wind_dir_deg       35394
avg_wind_speed_kmh     22472
dtype: int64

In [ ]:
data.describe()

avg_temp_c     min_temp_c     max_temp_c precipitation_mm  \
count  182338.000000  182338.000000  182338.000000         182338.0   
mean       19.137516      14.627775      23.887261         3.679964   
std         9.902722      10.004998      10.446670        11.294167   
min       -34.700000     -43.800000     -28.500000              0.0   
25%        12.500000       7.800000      17.700000              0.0   
50%        21.600000      16.700000      27.500000              4.1   
75%        27.200000      24.000000      32.000000             <NA>   
max        41.900000      38.900000      49.100000            496.1   

      snow_depth_mm  avg_wind_dir_deg  avg_wind_speed_kmh  
count      182338.0     182338.000000       182338.000000  
mean     342.481696        175.650289           11.281875  
std     1020.265388        105.435150            6.132884  
min             0.0          0.000000            0.000000  
25%            <NA>        100.000000            7.600000  
50%            <NA>        221.000000           10.900000  
75%            <NA>        334.000000           17.100000  
max          7140.0        360.000000           80.000000

#

In [ ]:
# Import Libraries
# Import libraries for data manipulation and analysis
import pandas as pd
# Import library for numerical operations
import numpy as np
# Import library for time series forecasting from statsmodels
from statsmodels.tsa.statespace.sarimax import SARIMAX
# Import library for regression tasks from scikit-learn
from sklearn.ensemble import RandomForestRegressor
# Import library for handling missing values from scikit-learn
from sklearn.impute import SimpleImputer
# Import library for XGBoost implementation from xgboost
import xgboost as xgb
# Import library for progress bars in loops
from tqdm import tqdm
# Import library for managing warning messages
import warnings

In [ ]:
# Ignore Future Warnings
warnings.filterwarnings("ignore", category=FutureWarning)

In [ ]:
# Load the Datasets
historical_weather = pd.read_csv('historical_weather.csv') # historical weather data data
submission_key = pd.read_csv('submission_key.csv') # To Mapping of submission_ID to city_id and date.

In [ ]:
# Print Column Names
# print("Columns in historical_weather:", historical_weather.columns)

In [ ]:
# Data Preparation
historical_weather.interpolate(method='linear', inplace=True) # interpolate fills missing values in historical_weather using linear interpolation.
# converts the date columns to datetime objects for both DataFrames.
historical_weather['date'] = pd.to_datetime(historical_weather['date'])
submission_key['date'] = pd.to_datetime(submission_key['date'])

In [ ]:
# Feature Engineering
'''
create_advanced_features function generates additional features for the DataFrame:
Extracts month, day_of_year, and year from the date.
Computes sine and cosine transformations for month and day_of_year to capture seasonality.
Calculates 7-day and 30-day rolling averages of avg_temp_c.
Creates lag features for avg_temp_c for specific lags (1, 2, 3, 7, 14, 30 days).
'''
def create_advanced_features(df):
    df['month'] = df['date'].dt.month
    df['day_of_year'] = df['date'].dt.dayofyear
    df['year'] = df['date'].dt.year
    df['month_sin'] = np.sin(df['month'] * (2 * np.pi / 12))
    df['month_cos'] = np.cos(df['month'] * (2 * np.pi / 12))
    df['day_sin'] = np.sin(df['day_of_year'] * (2 * np.pi / 365))
    df['day_cos'] = np.cos(df['day_of_year'] * (2 * np.pi / 365))

    # Add rolling averages
    df['temp_rolling_mean_7'] = df.groupby('city_id')['avg_temp_c'].rolling(window=7).mean().reset_index(0, drop=True)
    df['temp_rolling_mean_30'] = df.groupby('city_id')['avg_temp_c'].rolling(window=30).mean().reset_index(0, drop=True)

    # Expand lag features
    lags = [1, 2, 3, 7, 14, 30]
    for lag in lags:
        df[f'temp_lag_{lag}'] = df.groupby('city_id')['avg_temp_c'].shift(lag)

    return df

historical_weather = create_advanced_features(historical_weather)

In [ ]:
# SARIMA Model Forecasting
'''
This function trains a SARIMA model and makes predictions for a specific city:
Sets date as the index and converts it to a period index.
Defines and fits a SARIMA model.
Predicts avg_temp_c for the forecast dates and returns the results as a DataFrame with date and sarima_pred.
'''
def forecast_sarima(city_data, forecast_dates):
    city_data = city_data.copy()
    city_data.set_index('date', inplace=True)
    city_data.index = pd.DatetimeIndex(city_data.index).to_period('D')
    model = SARIMAX(city_data['avg_temp_c'], order=(1, 1, 1), seasonal_order=(1, 1, 1, 12))
    model_fit = model.fit(disp=False)
    forecast_dates_period = pd.DatetimeIndex(forecast_dates).to_period('D')
    forecast = model_fit.predict(start=forecast_dates_period.min(), end=forecast_dates_period.max(), dynamic=True)
    forecast = forecast.to_timestamp().reset_index()
    forecast.columns = ['date', 'sarima_pred']
    return forecast

In [ ]:
# Random Forest Model Forecasting
'''
This function trains a Random Forest model and makes predictions:
Selects relevant features and handles missing values using SimpleImputer.
Trains a RandomForestRegressor.
Prepares the forecast features and iterates over the forecast dates to create lag features dynamically.
Predicts avg_temp_c for each forecast date and returns the results as a DataFrame with date and rf_pred.
'''
def forecast_rf(city_data, forecast_dates):
    features = ['month_sin', 'month_cos', 'day_sin', 'day_cos', 'temp_lag_1', 'temp_lag_2', 'temp_lag_3', 'temp_lag_7',
                'temp_rolling_mean_7', 'temp_rolling_mean_30']

    X = city_data[features]
    y = city_data['avg_temp_c']

    imputer = SimpleImputer(strategy='mean')
    X_imputed = imputer.fit_transform(X)

    model = RandomForestRegressor(n_estimators=100, random_state=42)
    model.fit(X_imputed, y)

    forecast_features = create_advanced_features(pd.DataFrame({'date': forecast_dates, 'city_id': city_data['city_id'].iloc[0], 'avg_temp_c': np.nan}))

    # Create lag features for forecast dates
    last_known_temps = city_data.sort_values('date').tail(30)['avg_temp_c'].tolist()
    forecast_temps = []

    for i in range(len(forecast_dates)):
        temp_lags = last_known_temps[-30:]
        current_features = forecast_features.iloc[i].to_dict()
        for lag in [1, 2, 3, 7, 14, 30]:
            current_features[f'temp_lag_{lag}'] = temp_lags[-lag]
        current_features['temp_rolling_mean_7'] = np.mean(temp_lags[-7:])
        current_features['temp_rolling_mean_30'] = np.mean(temp_lags)

        current_features_array = np.array([current_features[f] for f in features]).reshape(1, -1)
        current_features_imputed = imputer.transform(current_features_array)
        temp_prediction = model.predict(current_features_imputed)[0]
        forecast_temps.append(temp_prediction)
        last_known_temps.append(temp_prediction)

    return pd.DataFrame({'date': forecast_dates, 'rf_pred': forecast_temps})


In [ ]:
# XGBoost Model Forecasting
# This function is similar to forecast_rf, but it uses an XGBoost model for predictions.

def forecast_xgb(city_data, forecast_dates):
    features = ['month_sin', 'month_cos', 'day_sin', 'day_cos', 'temp_lag_1', 'temp_lag_2', 'temp_lag_3', 'temp_lag_7',
                'temp_rolling_mean_7', 'temp_rolling_mean_30']

    X = city_data[features]
    y = city_data['avg_temp_c']

    imputer = SimpleImputer(strategy='mean')
    X_imputed = imputer.fit_transform(X)

    model = xgb.XGBRegressor(n_estimators=100, learning_rate=0.1, random_state=42)
    model.fit(X_imputed, y)

    forecast_features = create_advanced_features(pd.DataFrame({'date': forecast_dates, 'city_id': city_data['city_id'].iloc[0], 'avg_temp_c': np.nan}))

    # Create lag features for forecast dates
    last_known_temps = city_data.sort_values('date').tail(30)['avg_temp_c'].tolist()
    forecast_temps = []

    for i in range(len(forecast_dates)):
        temp_lags = last_known_temps[-30:]
        current_features = forecast_features.iloc[i].to_dict()
        for lag in [1, 2, 3, 7, 14, 30]:
            current_features[f'temp_lag_{lag}'] = temp_lags[-lag]
        current_features['temp_rolling_mean_7'] = np.mean(temp_lags[-7:])
        current_features['temp_rolling_mean_30'] = np.mean(temp_lags)

        current_features_array = np.array([current_features[f] for f in features]).reshape(1, -1)
        current_features_imputed = imputer.transform(current_features_array)
        temp_prediction = model.predict(current_features_imputed)[0]
        forecast_temps.append(temp_prediction)
        last_known_temps.append(temp_prediction)

    return pd.DataFrame({'date': forecast_dates, 'xgb_pred': forecast_temps})


In [ ]:
# Prepare the Submission DataFrame
'''
This loop iterates over each unique city_id:
Extracts city-specific data and forecast dates.
Calls the three forecasting functions (forecast_sarima, forecast_rf, forecast_xgb) to get predictions.
Merges the predictions into one DataFrame.
Averages the predictions from the three models to get the final predicted_avg_temp_c.
Adds the city_id to the forecast DataFrame and appends it to the predictions list.
'''
predictions = []
for city in tqdm(submission_key['city_id'].unique()):
    city_data = historical_weather[historical_weather['city_id'] == city]
    forecast_dates = submission_key[submission_key['city_id'] == city]['date']

    sarima_forecast = forecast_sarima(city_data, forecast_dates)
    rf_forecast = forecast_rf(city_data, forecast_dates)
    xgb_forecast = forecast_xgb(city_data, forecast_dates)

    city_forecast = pd.merge(sarima_forecast, rf_forecast, on='date')
    city_forecast = pd.merge(city_forecast, xgb_forecast, on='date')
    city_forecast['predicted_avg_temp_c'] = (city_forecast['sarima_pred'] + city_forecast['rf_pred'] + city_forecast['xgb_pred']) / 3
    city_forecast['city_id'] = city
    predictions.append(city_forecast)


  0%|          | 0/100 [00:00<?, ?it/s]/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but SimpleImputer was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but SimpleImputer was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but SimpleImputer was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but SimpleImputer was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but SimpleImputer was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning: X does 

In [ ]:
# Combine Predictions and Prepare Submission
'''
Concatenates all city predictions into a single DataFrame forecast_df.
Merges forecast_df with submission_key to align with the submission format.
Selects and renames the required columns for submission.
'''
forecast_df = pd.concat(predictions)
submission = pd.merge(submission_key, forecast_df[['city_id', 'date', 'predicted_avg_temp_c']], on=['city_id', 'date'])
submission = submission[['submission_ID', 'predicted_avg_temp_c']]
submission.columns = ['submission_ID', 'avg_temp_c']

In [ ]:
# Create Submission File
submission.to_csv('submission_improved.csv', index=False)

In [ ]:
# Prints the first few rows of the submission DataFrame to verify the output.
print(submission.head())

   submission_ID  avg_temp_c
0              1   11.534169
1              2   11.214116
2              3   10.924672
3              4   10.704878
4              5   10.681931


All in one with plot

In [ ]:
# All in one with plot

In [ ]:
import pandas as pd
import numpy as np
from statsmodels.tsa.statespace.sarimax import SARIMAX
from sklearn.ensemble import RandomForestRegressor
from sklearn.impute import SimpleImputer
import xgboost as xgb
from tqdm import tqdm
import warnings
import plotly.graph_objects as go
from plotly.subplots import make_subplots

warnings.filterwarnings("ignore", category=FutureWarning)

# Load the datasets
historical_weather = pd.read_csv('historical_weather.csv')
submission_key = pd.read_csv('submission_key.csv')

# Print column names
print("Columns in historical_weather:", historical_weather.columns)

# Data Preparation
historical_weather.interpolate(method='linear', inplace=True)
historical_weather['date'] = pd.to_datetime(historical_weather['date'])
submission_key['date'] = pd.to_datetime(submission_key['date'])

# Feature Engineering
def create_advanced_features(df):
    df['month'] = df['date'].dt.month
    df['day_of_year'] = df['date'].dt.dayofyear
    df['year'] = df['date'].dt.year
    df['month_sin'] = np.sin(df['month'] * (2 * np.pi / 12))
    df['month_cos'] = np.cos(df['month'] * (2 * np.pi / 12))
    df['day_sin'] = np.sin(df['day_of_year'] * (2 * np.pi / 365))
    df['day_cos'] = np.cos(df['day_of_year'] * (2 * np.pi / 365))

    # Add rolling averages
    df['temp_rolling_mean_7'] = df.groupby('city_id')['avg_temp_c'].rolling(window=7).mean().reset_index(0, drop=True)
    df['temp_rolling_mean_30'] = df.groupby('city_id')['avg_temp_c'].rolling(window=30).mean().reset_index(0, drop=True)

    # Expand lag features
    lags = [1, 2, 3, 7, 14, 30]
    for lag in lags:
        df[f'temp_lag_{lag}'] = df.groupby('city_id')['avg_temp_c'].shift(lag)

    return df

historical_weather = create_advanced_features(historical_weather)

# Function to train SARIMA model and make predictions
def forecast_sarima(city_data, forecast_dates):
    city_data = city_data.copy()
    city_data.set_index('date', inplace=True)
    city_data.index = pd.DatetimeIndex(city_data.index).to_period('D')
    model = SARIMAX(city_data['avg_temp_c'], order=(1, 1, 1), seasonal_order=(1, 1, 1, 12))
    model_fit = model.fit(disp=False)
    forecast_dates_period = pd.DatetimeIndex(forecast_dates).to_period('D')
    forecast = model_fit.predict(start=forecast_dates_period.min(), end=forecast_dates_period.max(), dynamic=True)
    forecast = forecast.to_timestamp().reset_index()
    forecast.columns = ['date', 'sarima_pred']
    return forecast

# Function to train Random Forest model and make predictions
def forecast_rf(city_data, forecast_dates):
    features = ['month_sin', 'month_cos', 'day_sin', 'day_cos', 'temp_lag_1', 'temp_lag_2', 'temp_lag_3', 'temp_lag_7',
                'temp_rolling_mean_7', 'temp_rolling_mean_30']

    X = city_data[features]
    y = city_data['avg_temp_c']

    imputer = SimpleImputer(strategy='mean')
    X_imputed = imputer.fit_transform(X)

    model = RandomForestRegressor(n_estimators=100, random_state=42)
    model.fit(X_imputed, y)

    forecast_features = create_advanced_features(pd.DataFrame({'date': forecast_dates, 'city_id': city_data['city_id'].iloc[0], 'avg_temp_c': np.nan}))

    # Create lag features for forecast dates
    last_known_temps = city_data.sort_values('date').tail(30)['avg_temp_c'].tolist()
    forecast_temps = []

    for i in range(len(forecast_dates)):
        temp_lags = last_known_temps[-30:]
        current_features = forecast_features.iloc[i].to_dict()
        for lag in [1, 2, 3, 7, 14, 30]:
            current_features[f'temp_lag_{lag}'] = temp_lags[-lag]
        current_features['temp_rolling_mean_7'] = np.mean(temp_lags[-7:])
        current_features['temp_rolling_mean_30'] = np.mean(temp_lags)

        current_features_array = np.array([current_features[f] for f in features]).reshape(1, -1)
        current_features_imputed = imputer.transform(current_features_array)
        temp_prediction = model.predict(current_features_imputed)[0]
        forecast_temps.append(temp_prediction)
        last_known_temps.append(temp_prediction)

    return pd.DataFrame({'date': forecast_dates, 'rf_pred': forecast_temps})

# Function to train XGBoost model and make predictions
def forecast_xgb(city_data, forecast_dates):
    features = ['month_sin', 'month_cos', 'day_sin', 'day_cos', 'temp_lag_1', 'temp_lag_2', 'temp_lag_3', 'temp_lag_7',
                'temp_rolling_mean_7', 'temp_rolling_mean_30']

    X = city_data[features]
    y = city_data['avg_temp_c']

    imputer = SimpleImputer(strategy='mean')
    X_imputed = imputer.fit_transform(X)

    model = xgb.XGBRegressor(n_estimators=100, learning_rate=0.1, random_state=42)
    model.fit(X_imputed, y)

    forecast_features = create_advanced_features(pd.DataFrame({'date': forecast_dates, 'city_id': city_data['city_id'].iloc[0], 'avg_temp_c': np.nan}))

    # Create lag features for forecast dates
    last_known_temps = city_data.sort_values('date').tail(30)['avg_temp_c'].tolist()
    forecast_temps = []

    for i in range(len(forecast_dates)):
        temp_lags = last_known_temps[-30:]
        current_features = forecast_features.iloc[i].to_dict()
        for lag in [1, 2, 3, 7, 14, 30]:
            current_features[f'temp_lag_{lag}'] = temp_lags[-lag]
        current_features['temp_rolling_mean_7'] = np.mean(temp_lags[-7:])
        current_features['temp_rolling_mean_30'] = np.mean(temp_lags)

        current_features_array = np.array([current_features[f] for f in features]).reshape(1, -1)
        current_features_imputed = imputer.transform(current_features_array)
        temp_prediction = model.predict(current_features_imputed)[0]
        forecast_temps.append(temp_prediction)
        last_known_temps.append(temp_prediction)

    return pd.DataFrame({'date': forecast_dates, 'xgb_pred': forecast_temps})

# Function to plot the forecasts using Plotly
def plot_forecasts(city_data, forecast_df, city_id):
    fig = make_subplots(rows=1, cols=1)

    fig.add_trace(go.Scatter(x=city_data['date'], y=city_data['avg_temp_c'], mode='lines', name='Historical Data'))
    fig.add_trace(go.Scatter(x=forecast_df['date'], y=forecast_df['sarima_pred'], mode='lines', name='SARIMA Prediction', line=dict(dash='dash')))
    fig.add_trace(go.Scatter(x=forecast_df['date'], y=forecast_df['rf_pred'], mode='lines', name='Random Forest Prediction', line=dict(dash='dash')))
    fig.add_trace(go.Scatter(x=forecast_df['date'], y=forecast_df['xgb_pred'], mode='lines', name='XGBoost Prediction', line=dict(dash='dash')))
    fig.add_trace(go.Scatter(x=forecast_df['date'], y=forecast_df['predicted_avg_temp_c'], mode='lines', name='Ensemble Prediction', line=dict(dash='dot')))

    fig.update_layout(
        title=f'City {city_id} - Temperature Forecast',
        xaxis_title='Date',
        yaxis_title='Average Temperature (°C)',
        legend_title='Legend',
        template='plotly_white'
    )

    fig.show()

# Prepare the submission DataFrame
predictions = []
for city in tqdm(submission_key['city_id'].unique()):
    city_data = historical_weather[historical_weather['city_id'] == city]
    forecast_dates = submission_key[submission_key['city_id'] == city]['date']

    sarima_forecast = forecast_sarima(city_data, forecast_dates)
    rf_forecast = forecast_rf(city_data, forecast_dates)
    xgb_forecast = forecast_xgb(city_data, forecast_dates)

    city_forecast = pd.merge(sarima_forecast, rf_forecast, on='date')
    city_forecast = pd.merge(city_forecast, xgb_forecast, on='date')
    city_forecast['predicted_avg_temp_c'] = (city_forecast['sarima_pred'] + city_forecast['rf_pred'] + city_forecast['xgb_pred']) / 3
    city_forecast['city_id'] = city
    predictions.append(city_forecast)

    # Plot the forecasts
    plot_forecasts(city_data, city_forecast, city)

forecast_df = pd.concat(predictions)
submission = pd.merge(submission_key, forecast_df[['city_id', 'date', 'predicted_avg_temp_c']], on=['city_id', 'date'])
submission = submission[['submission_ID', 'predicted_avg_temp_c']]
submission.columns = ['submission_ID', 'avg_temp_c']

# Create submission file
submission.to_csv('submission_improved.csv', index=False)

# Display the prepared submission DataFrame
print(submission.head())


Columns in historical_weather: Index(['city_id', 'date', 'avg_temp_c', 'min_temp_c', 'max_temp_c',
       'precipitation_mm', 'snow_depth_mm', 'avg_wind_dir_deg',
       'avg_wind_speed_kmh'],
      dtype='object')


  0%|          | 0/100 [00:00<?, ?it/s]/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature na

  1%|          | 1/100 [00:09<15:15,  9.24s/it]/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/statespace/kalman_filter.py:2473: ValueWarning:

Dynamic prediction specified to begin during out-of-sample forecasting period, and so has no effect.

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid featu

  2%|▏         | 2/100 [00:21<18:23, 11.26s/it]/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/statespace/kalman_filter.py:2473: ValueWarning:

Dynamic prediction specified to begin during out-of-sample forecasting period, and so has no effect.

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid featu

  3%|▎         | 3/100 [00:29<15:14,  9.42s/it]/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with fe

...

 97%|█████████▋| 97/100 [16:27<00:28,  9.36s/it]/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/statespace/kalman_filter.py:2473: ValueWarning:

Dynamic prediction specified to begin during out-of-sample forecasting period, and so has no effect.

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feat

 98%|█████████▊| 98/100 [16:35<00:17,  8.79s/it]/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/statespace/kalman_filter.py:2473: ValueWarning:

Dynamic prediction specified to begin during out-of-sample forecasting period, and so has no effect.

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feat

 99%|█████████▉| 99/100 [16:47<00:09,  9.87s/it]/usr/local/lib/python3.10/dist-packages/statsmodels/tsa/statespace/kalman_filter.py:2473: ValueWarning:

Dynamic prediction specified to begin during out-of-sample forecasting period, and so has no effect.

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feature names, but SimpleImputer was fitted with feature names

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:439: UserWarning:

X does not have valid feat

100%|██████████| 100/100 [16:59<00:00, 10.20s/it]

   submission_ID  avg_temp_c
0              1   11.534169
1              2   11.214116
2              3   10.924672
3              4   10.704878
4              5   10.681931
